# PRE-PROCESAMIENTO DE LOS DATOS

## IMPORTAR BIBLIOTECAS

In [1]:
import numpy as np
import pandas as pd
import sys
from pathlib import Path
from ydata_profiling import ProfileReport

In [2]:
current_dir = Path().resolve()
sys.path.append(str(current_dir.parent))

from config import RAW_DATA_PATH, PROCESSED_DATA_PATH
pd.options.display.max_columns = None

## IMPORTAR DATOS

In [3]:
original_data = pd.read_csv(RAW_DATA_PATH / 'lendingclub.csv', index_col=0)

C:\Users\SANTY\AppData\Local\Temp\ipykernel_6156\1782979593.py:1: DtypeWarning: Columns (20) have mixed types. Specify dtype option on import or set low_memory=False.
  original_data = pd.read_csv(RAW_DATA_PATH / 'lendingclub.csv', index_col=0)


In [4]:
data = original_data.copy()

## EXPLORACIÓN DE LOS DATOS

In [5]:
profile = ProfileReport(data, title='Lending Club', minimal=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


%|                                                                                           | 0/74 [00:00<?, ?it/s]
%|█                                                                                  | 1/74 [00:01<01:37,  1.34s/it]
%|██▏                                                                                | 2/74 [00:01<01:03,  1.13it/s]
100%|██████████████████████████████████████████████████████████████████████████████████| 74/74 [00:10<00:00,  6.96it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## PREPROCESAMIENTO

### LIMPIEZA Y TRANSFORMACIÓN DE DATOS CATEGORICOS MAL ESTRUCTURADOS EN TEXTO

In [6]:
data.term.unique()

array([' 36 months', ' 60 months'], dtype=object)

In [7]:
data.term = data.term.apply(lambda x: 36 if x == ' 36 months' else 60)

In [8]:
data.term.unique()

array([36, 60], dtype=int64)

In [9]:
data.emp_length.unique()

array(['10+ years', '< 1 year', '1 year', '3 years', '8 years', '9 years',
       '4 years', '5 years', '6 years', '2 years', '7 years', nan],
      dtype=object)

In [10]:
data.emp_length = data.emp_length.apply(lambda x: 0 if x == '< 1 year' or pd.isnull(x) else x[:2])
data.emp_length = pd.to_numeric(data.emp_length)

In [11]:
data.emp_length.unique()

array([10,  0,  1,  3,  8,  9,  4,  5,  6,  2,  7], dtype=int64)

### DANDO FORMATO A VARIABLES FECHA

In [12]:
data.issue_d

0         Dec-11
1         Dec-11
2         Dec-11
3         Dec-11
4         Dec-11
           ...  
466280    Jan-14
466281    Jan-14
466282    Jan-14
466283    Jan-14
466284    Jan-14
Name: issue_d, Length: 466285, dtype: object

In [13]:
data.issue_d = pd.to_datetime(data['issue_d'], format = '%b-%y')
data.issue_d

0        2011-12-01
1        2011-12-01
2        2011-12-01
3        2011-12-01
4        2011-12-01
            ...    
466280   2014-01-01
466281   2014-01-01
466282   2014-01-01
466283   2014-01-01
466284   2014-01-01
Name: issue_d, Length: 466285, dtype: datetime64[ns]

In [14]:
data['meses_credito'] = (pd.to_datetime('2022-01-01') - data.issue_d).dt.days / 30.44
data['meses_credito']

0         121.024967
1         121.024967
2         121.024967
3         121.024967
4         121.024967
             ...    
466280     95.992116
466281     95.992116
466282     95.992116
466283     95.992116
466284     95.992116
Name: meses_credito, Length: 466285, dtype: float64

In [15]:
from datetime import datetime

def corregir_fecha(fecha_str):
    try:
        fecha = datetime.strptime(fecha_str, '%b-%y')
        # Si el año es mayor a 2021, restar 100 años
        if fecha.year > 2021:
            fecha = fecha.replace(year=fecha.year - 100)
        return fecha
    except:
        return pd.NaT  # Por si hay errores de parsing

data['earliest_cr_line'] = data['earliest_cr_line'].apply(corregir_fecha)
data['linea_mesescredito'] = (pd.to_datetime('2021-01-01') - data['earliest_cr_line']).dt.days / 30.44                      

### OBTENIENDO DUMMIES PARA ALGUNAS VARIABLES CATEGORICAS

In [16]:
categorical_columns = ['home_ownership', 'purpose', 'grade', 'initial_list_status', 
                       'addr_state', 'loan_status', 'verification_status', 'sub_grade']
prefixs = ['home', 'purpose', 'grade', 'status_list', 
           'addr', 'loan_status', 'verification', 'sub_grade']

for col, pre in zip(categorical_columns, prefixs):
    # Convertir a minúsculas las categrorias
    if data[col].dtype == 'object' or pd.api.types.is_string_dtype(data[col]):
        data[col] = data[col].str.lower()
    
    data = pd.concat((
        data, 
        pd.get_dummies(data[col], prefix = pre, prefix_sep = '_', dtype=float)
    ), 
        axis=1
)
    # Reemplazar espacios en los nombres de columnas por guiones bajos
    data.columns = data.columns.str.replace(' ', '_', regex=False)

### DATOS FALTANTES - TRATANDO VARIABLES CON POCOS VALORES NULOS

In [17]:
pd.options.display.max_rows = None
data.isnull().sum()

id                                                                      0
member_id                                                               0
loan_amnt                                                               0
funded_amnt                                                             0
funded_amnt_inv                                                         0
term                                                                    0
int_rate                                                                0
installment                                                             0
grade                                                                   0
sub_grade                                                               0
emp_title                                                           27588
emp_length                                                              0
home_ownership                                                          0
annual_inc                            

In [18]:
pd.options.display.max_rows = 10
data.annual_inc = data.annual_inc.fillna(data.annual_inc.mean())

In [19]:
data.total_rev_hi_lim = data.total_rev_hi_lim.fillna(data.funded_amnt)

In [20]:
naas_columns = ['total_acc','acc_now_delinq', 'open_acc', 'delinq_2yrs', 
                'inq_last_6mths', 'pub_rec', 'linea_mesescredito']

data[naas_columns] = data[naas_columns].fillna(0)

### GUARDAR DATASET PROCESADO

In [21]:
data.to_csv(PROCESSED_DATA_PATH / 'lendingclub_processed.csv', index=False)